In [0]:
!pip3 install textblob

     |████████████████████████████████| 626 kB 4.7 MB/s 
     |████████████████████████████████| 1.5 MB 65.3 MB/s 
     |████████████████████████████████| 780 kB 41.6 MB/s 
     |████████████████████████████████| 78 kB 9.9 MB/s 
You should consider upgrading via the '/local_disk0/.ephemeral_nfs/envs/pythonEnv-5ea5edaf-a59e-4ada-bdd8-3dd1aac8f9ae/bin/python -m pip install --upgrade pip' command.


In [0]:
import os
DIRECTORY = "dbfs:/FileStore/tables"

# Reading and Cleaning Data File

In [0]:
from pyspark.sql import SparkSession
import pyspark.sql.functions as F
spark = SparkSession.builder.getOrCreate()
# We are explicitly calling out a few parameters in the SparkReader object. There are I think over 20 different parameters, but these should suffice for now 
file_location = "/FileStore/tables/All_Beauty.jsonl"
file_type = "text"

# CSV options
infer_schema = "false"
first_row_is_header = "false"
delimiter = ","

# The applied options are for CSV files. For other file types, these will be ignored.
reviewData = spark.read.format(file_type) \
  .option("inferSchema", infer_schema) \
  .option("header", first_row_is_header) \
  .option("sep", delimiter) \
  .load(file_location)

# display(reviewData)

In [0]:
from pyspark.sql.functions import from_json, col, schema_of_json

sample_json = reviewData.select("value").first()[0]
schema = schema_of_json(sample_json)

reviewDataExpanded = reviewData.withColumn("json_data", from_json(col("value"), schema)).select("json_data.*")

reviewDataExpanded.printSchema()


root
 |-- asin: string (nullable = true)
 |-- helpful_vote: long (nullable = true)
 |-- images: array (nullable = true)
 |    |-- element: string (containsNull = true)
 |-- parent_asin: string (nullable = true)
 |-- rating: double (nullable = true)
 |-- text: string (nullable = true)
 |-- timestamp: long (nullable = true)
 |-- title: string (nullable = true)
 |-- user_id: string (nullable = true)
 |-- verified_purchase: boolean (nullable = true)



In [0]:
reviewDataWithoutExtraColumns = reviewDataExpanded.drop(*["user_id", "images", "helpful_vote", "title"])

reviewDataWithoutExtraColumns.printSchema()

root
 |-- asin: string (nullable = true)
 |-- parent_asin: string (nullable = true)
 |-- rating: double (nullable = true)
 |-- text: string (nullable = true)
 |-- timestamp: long (nullable = true)
 |-- verified_purchase: boolean (nullable = true)



In [0]:
from pyspark.sql.functions import col, sum, when

# null_counts = reviewDataWithoutExtraColumns.select([sum(when(col(c).isNull(), 1).otherwise(0)).alias(c + "_null_count") for c in reviewDataWithoutExtraColumns.columns])

# null_counts.show()

# Reading and Cleaning Meta Data File

In [0]:


file_location = "/FileStore/tables/meta_All_Beauty.jsonl"
file_type = "text"

# CSV options
infer_schema = "false"
first_row_is_header = "false"
delimiter = ","

# The applied options are for CSV files. For other file types, these will be ignored.
metaData = spark.read.format(file_type) \
  .option("inferSchema", infer_schema) \
  .option("header", first_row_is_header) \
  .option("sep", delimiter) \
  .load(file_location)

display(metaData)

value {"main_category": "All Beauty", "title": "Howard LC0008 Leather Conditioner, 8-Ounce (4-Pack)", "average_rating": 4.8, "rating_number": 10, "features": [], "description": [], "price": null, "images": [{"thumb": "https://m.media-amazon.com/images/I/41qfjSfqNyL._SS40_.jpg", "large": "https://m.media-amazon.com/images/I/41qfjSfqNyL.jpg", "variant": "MAIN", "hi_res": null}, {"thumb": "https://m.media-amazon.com/images/I/41w2yznfuZL._SS40_.jpg", "large": "https://m.media-amazon.com/images/I/41w2yznfuZL.jpg", "variant": "PT01", "hi_res": "https://m.media-amazon.com/images/I/71i77AuI9xL._SL1500_.jpg"}], "videos": [], "store": "Howard Products", "categories": [], "details": {"Package Dimensions": "7.1 x 5.5 x 3 inches; 2.38 Pounds", "UPC": "617390882781"}, "parent_asin": "B01CUPMQZE", "bought_together": null} {"main_category": "All Beauty", "title": "Yes to Tomatoes Detoxifying Charcoal Cleanser (Pack of 2) with Charcoal Powder, Tomato Fruit Extract, and Gingko Biloba Leaf Extract, 5 fl. oz.", "average_rating": 4.5, "rating_number": 3, "features": [], "description": [], "price": null, "images": [{"thumb": "https://m.media-amazon.com/images/I/41b+11d5igL._SS40_.jpg", "large": "https://m.media-amazon.com/images/I/41b+11d5igL.jpg", "variant": "MAIN", "hi_res": "https://m.media-amazon.com/images/I/71g1lP0pMbL._SL1500_.jpg"}, {"thumb": "https://m.media-amazon.com/images/I/41j2ocUzCtL._SS40_.jpg", "large": "https://m.media-amazon.com/images/I/41j2ocUzCtL.jpg", "variant": "PT01", "hi_res": "https://m.media-amazon.com/images/I/81OqvR94isL._SL1500_.jpg"}], "videos": [], "store": "Yes To", "categories": [], "details": {"Item Form": "Powder", "Skin Type": "Acne Prone", "Brand": "Yes To", "Age Range (Description)": "Adult", "Unit Count": "10 Fl Oz", "Is Discontinued By Manufacturer": "No", "Item model number": "SG_B076WQZGPM_US", "UPC": "653801351125", "Manufacturer": "Yes to Tomatoes"}, "parent_asin": "B076WQZGPM", "bought_together": null} {"main_category": "All Beauty", "title": "Eye Patch Black Adult with Tie Band (6 Per Pack)", "average_rating": 4.4, "rating_number": 26, "features": [], "description": [], "price": null, "images": [{"thumb": "https://m.media-amazon.com/images/I/31bz+uqzWCL._SS40_.jpg", "large": "https://m.media-amazon.com/images/I/31bz+uqzWCL.jpg", "variant": "MAIN", "hi_res": null}, {"thumb": "https://m.media-amazon.com/images/I/31bz+uqzWCL._SS40_.jpg", "large": "https://m.media-amazon.com/images/I/31bz+uqzWCL.jpg", "variant": "PT01", "hi_res": null}], "videos": [], "store": "Levine Health Products", "categories": [], "details": {"Manufacturer": "Levine Health Products"}, "parent_asin": "B000B658RI", "bought_together": null} {"main_category": "All Beauty", "title": "Tattoo Eyebrow Stickers, Waterproof Eyebrow, 4D Imitation Eyebrow Tattoos, 4D Hair-like Authentic Eyebrows Waterproof Long Lasting for Woman & Man Makeup Tool", "average_rating": 3.1, "rating_number": 102, "features": [], "description": [], "price": null, "images": [{"thumb": "https://m.media-amazon.com/images/I/515iwxdKS1L._SS40_.jpg", "large": "https://m.media-amazon.com/images/I/515iwxdKS1L.jpg", "variant": "MAIN", "hi_res": "https://m.media-amazon.com/images/I/71GJhXQGvyL._SL1500_.jpg"}, {"thumb": "https://m.media-amazon.com/images/I/51ALSVnGDML._SS40_.jpg", "large": "https://m.media-amazon.com/images/I/51ALSVnGDML.jpg", "variant": "PT01", "hi_res": "https://m.media-amazon.com/images/I/61NS1lONhzL._SL1001_.jpg"}, {"thumb": "https://m.media-amazon.com/images/I/51GvPall-ML._SS40_.jpg", "large": "https://m.media-amazon.com/images/I/51GvPall-ML.jpg", "variant": "PT02", "hi_res": "https://m.media-amazon.com/images/I/61lcwXtw3ZL._SL1001_.jpg"}, {"thumb": "https://m.media-amazon.com/images/I/51JFEUql-KL._SS40_.jpg", "large": "https://m.media-amazon.com/images/I/51JFEUql-KL.jpg", "variant": "PT03", "hi_res": "https://m.media-amazon.com/images/I/61G-iZeX-LL._SL1001_.jpg"}, {"thumb": "https://m.media-amazon.com/images/I/414rIT4vNAL._SS40_.jpg", "large": "https://m

In [0]:
from pyspark.sql.functions import from_json, col, schema_of_json

sample_json = metaData.select("value").first()[0]
schema = schema_of_json(sample_json)

metaDataExpanded = metaData.withColumn("json_data", from_json(col("value"), schema)).select("json_data.*")

# metaDataExpanded.show()

In [0]:
metaDataWithoutExtraColumns = metaDataExpanded.drop(*[ "images", "videos","features", "bought_together", "description", "store", "details"])

# metaDataWithoutExtraColumns.show(1)

In [0]:

# null_counts = metaDataWithoutExtraColumns.select([sum(when(col(c).isNull(), 1).otherwise(0)).alias(c + "_null_count") for c in metaDataWithoutExtraColumns.columns])

# null_counts.show()

In [0]:
# null_counts_not = metaDataWithoutExtraColumns.select([sum(when(col(c).isNotNull(), 1).otherwise(0)).alias(c + "not_null_count") for c in metaDataWithoutExtraColumns.columns])

# null_counts_not.select("pricenot_null_count").show()

In [0]:
metaDataNotNull = metaDataWithoutExtraColumns.dropna(subset=["price"])

In [0]:
# metaDataNotNull.show()

Broadcast List of words

In [0]:
# Define your list of price-related words and their weights
price_words = {
    'expensive': 2.0,
    'cheap': 2.0,
    'overpriced': 2.5,
    'affordable': 1.5,
    'costly': 2.0,
    'inexpensive': 1.5,
    'budget': 1.5,
    'pricey': 2.0,
    # Add more words and adjust weights as needed
}

# Broadcast the price_words dictionary
price_words_broadcast = spark.sparkContext.broadcast(price_words)


# Starting the Calculation of Sentiment Score

In [0]:
from pyspark.sql.types import DoubleType
from pyspark.sql.functions import udf, col
from textblob import TextBlob
import re

# Define the UDF to compute the weighted sentiment score
def get_weighted_sentiment(text):
    # Clean and tokenize the text
    words = re.findall(r'\w+', text.lower())
    
    # Initialize sentiment components
    base_sentiment = TextBlob(text).sentiment.polarity
    weighted_sentiment = base_sentiment
    price_word_count = 0

    # Get the broadcasted price words dictionary
    price_words = price_words_broadcast.value

    # Adjust sentiment based on price-related words
    for word in words:
        if word in price_words:
            weight = price_words[word]
            # You can choose how to adjust the sentiment:
            # Option 1: Multiply the base sentiment
            weighted_sentiment += base_sentiment * (weight - 1)
            # Option 2: Add or subtract a fixed value
            # weighted_sentiment += base_sentiment + weight
            price_word_count += 1

    # Optionally, normalize the sentiment score
    if price_word_count > 0:
        weighted_sentiment = weighted_sentiment / price_word_count

    return weighted_sentiment

# Register the UDF
weighted_sentiment_udf = udf(get_weighted_sentiment, DoubleType())

# weighted_sentiment_udf.show()


In [0]:
# Apply the UDF to compute the weighted sentiment score
reviewDataWithWeightedSentiment = reviewDataWithoutExtraColumns.withColumn(
    "weighted_sentiment_score", weighted_sentiment_udf(col("text"))
)


In [0]:
reviewDataWithWeightedSentiment.show()

+----------+-----------+------+--------------------+-------------+-----------------+------------------------+
|      asin|parent_asin|rating|                text|    timestamp|verified_purchase|weighted_sentiment_score|
+----------+-----------+------+--------------------+-------------+-----------------+------------------------+
|B00YQ6X8EO| B00YQ6X8EO|   5.0|This spray is rea...|1588687728923|             true|     0.39010416666666664|
|B081TJ8YS3| B081TJ8YS3|   4.0|This product does...|1588615855070|             true|                    0.25|
|B07PNNCSP9| B097R46CSY|   5.0|Smells good, feel...|1589665266052|             true|                    0.85|
|B09JS339BZ| B09JS339BZ|   1.0|      Felt synthetic|1643393630220|             true|                     0.0|
|B08BZ63GMJ| B08BZ63GMJ|   5.0|             Love it|1609322563534|             true|                     0.5|
|B00R8DXL44| B00R8DXL44|   4.0|The polish was qu...|1598567408138|             true|    -0.04444444444444445|
|B099DRHW5

In [0]:
from pyspark.sql.functions import size, split

reviewDataWithWordCount = reviewDataWithWeightedSentiment.withColumn("word_count", size(split("text", " ")))

In [0]:
from pyspark.ml.feature import Tokenizer, HashingTF, IDF

# Tokenize text
tokenizer = Tokenizer(inputCol="text", outputCol="words")
wordsData = tokenizer.transform(reviewDataWithWordCount)

# Calculate TF
hashingTF = HashingTF(inputCol="words", outputCol="raw_features", numFeatures=1000)
featurizedData = hashingTF.transform(wordsData)

# Calculate IDF
idf = IDF(inputCol="raw_features", outputCol="tfidf_features")
idfModel = idf.fit(featurizedData)
reviewDataWithTFIDF = idfModel.transform(featurizedData)

In [0]:
# reviewDataWithTFIDF.show()

In [0]:
from pyspark.sql.functions import avg

# Average sentiment per product
productSentimentData = reviewDataWithTFIDF.groupBy("asin").agg(avg("weighted_sentiment_score").alias("avg_sentiment_score"), avg("rating").alias("avg_rating"))

In [0]:
productSentimentData.show()

+----------+-------------------+------------------+
|      asin|avg_sentiment_score|        avg_rating|
+----------+-------------------+------------------+
|B08ZSR9HLF|0.24874500747268602| 4.142857142857143|
|B094VG2GKR| 0.2416666666666667|               3.0|
|B07K1LGWYB|0.22255527210884354|3.5714285714285716|
|B0B8DB17VT|0.28761716046290703| 4.409090909090909|
|B085M95TX2| 0.2174915231468373| 3.909090909090909|
|B07YS9W97B|0.26438571275872863| 4.666666666666667|
|B00TK0VV68| 0.3106084584930739|4.6923076923076925|
|B00VUIVWA8|              0.375|               5.0|
|B07MMWXPLJ|0.29316543382222576| 4.502890173410405|
|B07HCR8QDN|0.21104166666666668|               5.0|
|B07M6LSZVF|0.39504714035964034|             4.875|
|B07Y9KVKFK|                1.0|               5.0|
|B07SPDDDZT| 0.3016174123495552|             4.125|
|B07K1DRCYR| 0.3245891228771988| 4.098802395209581|
|B000FEF1V4|0.21217270809382588| 4.127035830618892|
|B087GD4BJ1|0.21941464351552983|              3.75|
|B08CZD385F|

In [0]:
from pyspark.sql.functions import from_unixtime, year, month

reviewDataWithDate = reviewDataWithTFIDF.withColumn("date", from_unixtime("timestamp"))
reviewDataWithYearMonth = reviewDataWithDate.withColumn("year", year("date")).withColumn("month", month("date"))

In [0]:
productSentimentTrend = reviewDataWithYearMonth.groupBy("asin", "year", "month").agg(avg("weighted_sentiment_score").alias("avg_sentiment_over_time"))

In [0]:
productSentimentTrend.show()

+----------+-----+-----+-----------------------+
|      asin| year|month|avg_sentiment_over_time|
+----------+-----+-----+-----------------------+
|B08LYT4Q2X|52865|    5|     0.5687500000000001|
|B07LCHCD6Q|51298|    5|    0.22976190476190475|
|B07WV6JHVM|52098|    2|   -0.07500000000000001|
|B09HTPJ5PJ|54118|    5|    0.24404761904761907|
|B00BS473N4|49833|    8|     0.4488095238095238|
|B005B6GCN2|47035|   10|                    0.7|
|B07DFNPVSF|52590|    5|    0.06499999999999999|
|B01C74U1UU|50741|    7|   -0.05000000000000001|
|B01D6O4Y12|53259|    3|     0.4510204081632653|
|B09CLNDMXX|54419|   11|     0.1272516835016835|
|B09NFKDCPG|54764|   12|    0.19722222222222224|
|B07WLPT67K|51986|   11|                 -0.205|
|B08WJPNZPQ|54123|   12|   -0.03333333333333...|
|B088B4KSW8|52765|    4|                   0.35|
|B0993XRX8X|53792|    2|     0.2733333333333333|
|B00ZUD4B5C|48878|    5|                  0.275|
|B07871RLLG|52669|    7|    0.20088757396449708|
|B076QY8N23|50942|  

In [0]:
final_data = productSentimentData.join(metaDataNotNull, productSentimentData["asin"] == metaDataNotNull["parent_asin"])

In [0]:
final_data.show()

+----------+--------------------+------------------+--------------+----------+-------------+-----------+------+-------------+--------------------+
|      asin| avg_sentiment_score|        avg_rating|average_rating|categories|main_category|parent_asin| price|rating_number|               title|
+----------+--------------------+------------------+--------------+----------+-------------+-----------+------+-------------+--------------------+
|B07MMWXPLJ| 0.29316543382222576| 4.502890173410405|           4.7|        []|   All Beauty| B07MMWXPLJ| 16.95|         1355|Aveeno Repairing ...|
|B07M6LSZVF| 0.39504714035964034|             4.875|           4.9|        []|   All Beauty| B07M6LSZVF|  18.2|           33|Michel Design Wor...|
|B07KFNQ33H| 0.38000086613179285|4.7011494252873565|           4.6|        []|   All Beauty| B07KFNQ33H|  24.0|          785|L’ange Hair Borag...|
|B00NFUDWBQ| 0.46067206672637706|               4.2|           4.2|        []|   All Beauty| B00NFUDWBQ| 19.99|       

In [0]:
from pyspark.sql.functions import avg, col, concat_ws, lit, when, row_number, rand, ceil, array, element_at, log
from pyspark.sql.window import Window
import itertools

In [0]:
alpha = 0.1      # Learning rate
gamma = 0.9      # Discount factor
epsilon = 0.1    # Exploration rate
num_epochs = 6  # Number of training epochs

# Define action space
actions = ["increase", "decrease", "maintain"]

In [0]:
# Coefficients for dynamic multiplier calculations
coeff_a = 0.02    # Coefficient for sentiment score
coeff_b = 0.01    # Coefficient for average rating
coeff_c = 0.0005  # Coefficient for log(rating_number)

In [0]:
pricingDataBinned = final_data.withColumn(
    "sentiment_bin",
    when(col("avg_sentiment_score") > 0.5, "high")
    .when(col("avg_sentiment_score") < -0.5, "low")
    .otherwise("medium")
).withColumn(
    "rating_bin",
    when(col("avg_rating") >= 4.5, "high")
    .when(col("avg_rating") <= 2.5, "low")
    .otherwise("medium")
).withColumn(
    "state",
    concat_ws("_", col("sentiment_bin"), col("rating_bin"))
)

pricingDataBinned.cache()


Out[31]: DataFrame[asin: string, avg_sentiment_score: double, avg_rating: double, average_rating: double, categories: array<string>, main_category: string, parent_asin: string, price: string, rating_number: bigint, title: string, sentiment_bin: string, rating_bin: string, state: string]

In [0]:
pricingDataBinned.show()

+----------+-------------------+------------------+--------------+----------+-------------+-----------+------+-------------+--------------------+-------------+----------+-------------+
|      asin|avg_sentiment_score|        avg_rating|average_rating|categories|main_category|parent_asin| price|rating_number|               title|sentiment_bin|rating_bin|        state|
+----------+-------------------+------------------+--------------+----------+-------------+-----------+------+-------------+--------------------+-------------+----------+-------------+
|B000UI9GTS|0.19805555555555557| 4.666666666666667|           4.6|        []|   All Beauty| B000UI9GTS|195.99|            4|Mariner 2 Chrome ...|       medium|      high|  medium_high|
|B00195R3F0|                0.0|               2.0|           2.0|        []|   All Beauty| B00195R3F0|  5.99|            1|2008 Surfside Coo...|       medium|       low|   medium_low|
|B003814C1Q| 0.4521967780896352| 4.538461538461538|           4.0|        [

In [0]:
# Extract distinct states
states = pricingDataBinned.select("state").distinct().collect()
states = [row['state'] for row in states]

# Initialize Q-Table with all state-action pairs
q_table = spark.createDataFrame(
    [(state, action, 0.0) for state, action in itertools.product(states, actions)],
    ["state", "action", "Q_value"]
).cache()

In [0]:
from pyspark.sql.functions import log as spark_log

for epoch in range(num_epochs):
    print(f"Epoch {epoch + 1} / {num_epochs}")

    # Join pricing data with Q-table
    joined = pricingDataBinned.join(
        q_table,
        on=["state"],
        how="left"
    )

    # Epsilon-greedy action selection
    joined = joined.withColumn(
        "explore",
        (rand() < lit(epsilon)).cast("integer")
    )

    # Determine best action per asin based on current Q-values
    windowSpec = Window.partitionBy("asin").orderBy(col("Q_value").desc())
    best_actions = joined.withColumn(
        "rank",
        row_number().over(windowSpec)
    ).filter(col("rank") == 1).select("asin", "action", "explore").withColumnRenamed("action", "best_action")

    # Assign actions to asins
    pricingWithBestAction = pricingDataBinned.join(best_actions, on="asin", how="left")

    # Assign random actions for exploration
    pricingWithActions = pricingWithBestAction.withColumn(
    "action",
    when(
        col("explore") == 1,
        element_at(array(*[lit(act) for act in actions]), ceil(rand() * len(actions)).cast("int")).cast("string")
    ).otherwise(col("best_action"))
    )

    # Calculate dynamic multipliers
    # Prevent divide-by-zero by adding a small constant to rating_number
    pricingWithActions = pricingWithActions.withColumn(
        "log_rating_number",
        spark_log(col("rating_number") + 1)
    )

    pricingWithActions = pricingWithActions.withColumn(
        "increase_multiplier",
        1 + (coeff_a * col("avg_sentiment_score")) + 
            (coeff_b * col("avg_rating")) - 
            (coeff_c * col("log_rating_number"))
    ).withColumn(
        "decrease_multiplier",
        1 - (coeff_a * col("avg_sentiment_score")) - 
            (coeff_b * col("avg_rating")) + 
            (coeff_c * col("log_rating_number"))
    )

    # Cap the multipliers to prevent extreme price changes
    pricingWithActions = pricingWithActions.withColumn(
        "increase_multiplier",
        when(col("increase_multiplier") > 1.2, 1.2)
        .when(col("increase_multiplier") < 1.0, 1.0)
        .otherwise(col("increase_multiplier"))
    ).withColumn(
        "decrease_multiplier",
        when(col("decrease_multiplier") < 0.8, 0.8)
        .when(col("decrease_multiplier") > 1.0, 1.0)
        .otherwise(col("decrease_multiplier"))
    )

    # Apply action and compute new_price based on dynamic multipliers
    pricingWithActions = pricingWithActions.withColumn(
        "new_price",
        when(col("action") == "increase", (col("price") * col("increase_multiplier")).cast("double"))
        .when(col("action") == "decrease", (col("price") * col("decrease_multiplier")).cast("double"))
        .otherwise(col("price") * lit(1.0))
    )

    # Simulate reward using 'rating_number' as proxy for sales volume
    # Here, assume revenue as reward
    pricingWithActions = pricingWithActions.withColumn(
        "reward",
        col("rating_number") * col("new_price")
    )

    # Aggregate rewards per state and action
    rewards = pricingWithActions.groupBy("state", "action").agg(
        avg("reward").alias("avg_reward")
    )

    # Update Q-table based on the aggregated rewards
    # Join Q-table with rewards
    q_table_updated = q_table.join(
        rewards,
        on=["state", "action"],
        how="left"
    ).withColumn(
        "Q_value",
        when(
            col("avg_reward").isNotNull(),
            col("Q_value") + alpha * (
                col("avg_reward") + gamma * q_table.filter(q_table.state == col("state")).select("Q_value").agg({"Q_value": "max"}).collect()[0][0] - col("Q_value")
            )
        ).otherwise(col("Q_value"))
    ).select("state", "action", "Q_value")

    q_table = q_table_updated.cache()

    print(f"Completed Epoch {epoch + 1}")

Epoch 1 / 6
Completed Epoch 1
Epoch 2 / 6
Completed Epoch 2
Epoch 3 / 6
Completed Epoch 3
Epoch 4 / 6
Completed Epoch 4
Epoch 5 / 6
Completed Epoch 5
Epoch 6 / 6
Completed Epoch 6


In [0]:
q_table.show()

+-------------+--------+------------------+
|        state|  action|           Q_value|
+-------------+--------+------------------+
|  high_medium|increase| 689.5443279965741|
|medium_medium|decrease|1856.6806438975516|
|  high_medium|maintain| 907.4792038593251|
|    high_high|maintain| 901.7896683739361|
|   low_medium|increase| 275.2505594848981|
|  medium_high|increase|1178.6706936537455|
|  medium_high|decrease| 960.1108032454232|
|  medium_high|maintain|1159.3748654080914|
|   low_medium|maintain| 517.9137395281142|
|     low_high|decrease|119.65483087931148|
|     low_high|maintain| 477.3065454692571|
|      low_low|decrease| 669.8951375040446|
|    high_high|decrease| 790.0100066055365|
|    high_high|increase| 648.1104631640412|
|   low_medium|decrease|               0.0|
|  high_medium|decrease| 775.7938682815474|
|     low_high|increase| 273.8931554095632|
|   medium_low|decrease| 949.5085874110047|
|   medium_low|maintain|  1422.93610675621|
|   medium_low|increase|1359.231

In [0]:
pricingWithActions.select(["asin", "avg_rating","avg_sentiment_score", "best_action","price", "new_price"]).show()

+----------+------------------+-------------------+-----------+------+------------------+
|      asin|        avg_rating|avg_sentiment_score|best_action| price|         new_price|
+----------+------------------+-------------------+-----------+------+------------------+
|B000UI9GTS| 4.666666666666667|0.19805555555555557|   increase|195.99| 205.7548212984377|
|B00195R3F0|               2.0|                0.0|   increase|  5.99| 6.107724024194224|
|B003814C1Q| 4.538461538461538| 0.4521967780896352|   increase| 26.96|28.388431522218717|
|B0041M6VHE|               5.0|                0.4|   increase| 21.84| 23.07156987599244|
|B00535I48C|               4.0|              0.125|   maintain| 38.99|             38.99|
|B009H71WAE|               4.0| 0.5254166666666666|   maintain|  13.5|              13.5|
|B00GMOT7PM|               4.0|              0.375|   maintain| 23.03|             23.03|
|B00GMP6OKW|               4.0| 0.3494047619047619|   maintain|  9.75|              9.75|
|B00HJD0MY

In [0]:
rewards.show()

+-------------+--------+------------------+
|        state|  action|        avg_reward|
+-------------+--------+------------------+
|medium_medium|decrease|3838.2211621778997|
|  high_medium|maintain|1121.2359999999996|
|    high_high|maintain|1119.4421459433504|
|  medium_high|increase|1618.0641779797459|
|  medium_high|maintain|1725.7762962962963|
|    high_high|increase|480.02675465950955|
|   medium_low|decrease| 537.0452732540135|
|   medium_low|increase|1073.6150793244212|
|medium_medium|maintain|3047.4680715781437|
|  medium_high|decrease|1036.5834795415622|
|      low_low|decrease| 474.4798760402162|
|    high_high|decrease| 916.4137448059826|
|medium_medium|increase| 2060.749278516929|
|     high_low|decrease| 736.6985539912184|
|   medium_low|maintain| 3786.109074074074|
|     low_high|maintain|223.23000000000002|
|     high_low|maintain|209.26500000000001|
|  high_medium|increase|264.87242749126113|
|  high_medium|decrease|1400.9412421336374|
|      low_low|increase|        

In [0]:
cumulative_reward = rewards.agg(F.sum("avg_reward").alias("cumulative_reward"))
cumulative_reward.show()

+-----------------+
|cumulative_reward|
+-----------------+
|26449.55806015348|
+-----------------+



In [0]:
total_reward = pricingWithActions.agg(F.sum("reward").alias("total_reward"))
total_reward.show()

+-------------------+
|       total_reward|
+-------------------+
|3.188722298885839E7|
+-------------------+

